In [ ]:
%matplotlib notebook
import os
import itertools
import numpy as np
import pandas as pd
import plotly.express as px
import json
import matplotlib.pyplot as plt
# from vehicle.common.config.vehicle_config_run import get_hardware_config_run   # only loads on vehicle runs, not useful
from base.geometry.transformations import quaternion_from_euler

In [ ]:
acceleration_factor = 50

data = pd.DataFrame(
[
#     "20190905T000503-kitt_21", camera cal frame selection stage fail, json not availble
    ("20190906T162609-kitt_21", acceleration_factor * 209.7625),
    ("20190909T113621-kitt_21", acceleration_factor * 565.4),
    ("20190911T131044-kitt_21", acceleration_factor * 905.525),
    ("20190914T130900-kitt_21", acceleration_factor * 1451.825),
    ("20190917T123429-kitt_21", acceleration_factor * 1886.525),
    ("20190923T175925-kitt_21", acceleration_factor * 2012.525),
#     ("20191210T232924-kitt_21", ), # 
], columns=("meta_id", "miles"))

In [ ]:
WORKSPACE_ROOT = "/mnt/nautilus_rw/CLAMS/chandler/mga_calibration"
lidar_column_names = ["lidar", "x", "y", "z", "roll", "pitch", "yaw"]

def json_path_from_meta_id(meta_id):
    return os.path.join(WORKSPACE_ROOT, meta_id + '-dclams', "vehicle_config_after_camera_calibration.json")

def json_from_json_path(json_path):
    with open(json_path, 'r') as f:
        return json.load(f)
    
def lidar_df_from_lidar_list(lidar_list):
    output = pd.DataFrame()
    for lidar_idx, lidar in enumerate(lidar_list):
        extrinsics = lidar['extrinsics']['extrinsics']
        row_df = pd.DataFrame({
            "lidar": [lidar['position']],
            "pitch": [extrinsics['euler_rotation']['pitch_radians']],
            "roll": [extrinsics['euler_rotation']['roll_radians']],
            "yaw": [extrinsics['euler_rotation']['yaw_radians']],
            "x": [extrinsics['translation']['x']],
            "y": [extrinsics['translation']['y']],
            "z": [extrinsics['translation']['z']],
        }, columns=lidar_column_names)
        output = output.append(row_df, ignore_index=True)
    return output


In [ ]:
extrinsics_df = pd.DataFrame(columns=list(data.columns) + lidar_column_names)
for _, row in data.iterrows():
    meta_id, _ = row
    json_data = json_from_json_path(json_path_from_meta_id(meta_id))
    meta_id_extrinsics_df = lidar_df_from_lidar_list(json_data['lidar'])
    for col in data.columns:
        meta_id_extrinsics_df[col] = row[col]

    # https://stackoverflow.com/a/40405548 because pandas is wacky
    extrinsics_df = extrinsics_df.append(meta_id_extrinsics_df, ignore_index=True)[list(extrinsics_df.columns)]
extrinsics_df = extrinsics_df.sort_values(by=['miles', 'lidar'])

In [ ]:
def get_lidar_relative_extrinsics(extrinsics_df):
    """
    Rather than showing extrinsics as relative to base link, make them relative to the FRONT_LOWER_CENTER lidar.
    """
    delta_extrinsics_df = pd.DataFrame()
    dims = ['x', 'y', 'z', 'roll', 'pitch', 'yaw']
    for meta_id, meta_id_df in extrinsics_df.groupby('meta_id'):
        meta_id_df = meta_id_df.copy()
        lidar_flc = meta_id_df.query('lidar == "FRONT_LOWER_CENTER"')
        
        # iloc[0] converts df to series which permits subtraction broadcast across rows
        meta_id_df[dims] = meta_id_df[dims] - lidar_flc[dims].iloc[0]
        delta_extrinsics_df = delta_extrinsics_df.append(meta_id_df)

    return delta_extrinsics_df

extrinsics_L = get_lidar_relative_extrinsics(extrinsics_df)
        

In [ ]:
# def delta_euler_angle(rpy_rad1, rpy_rad2):
#     q1, q2 = quaternion_from_euler(*rpy_rad1), quaternion_from_euler(*rpy_rad2)
#     print q1, q2
# delta_euler_angle([0,0,0],[1,0,1])

non_numeric_columns = ['meta_id_a', 'meta_id_b', 'lidar']
numeric_columns = ['miles', 'x', 'y', 'z', 'roll', 'pitch', 'yaw']
def pairwise(iterable):
    # https://stackoverflow.com/a/5434936
    "s -> (s0,s1), (s1,s2), (s2, s3), ..."
    a, b = itertools.tee(iterable)
    next(b, None)
    return itertools.izip(a, b)

# def get_delta_extrinsics_per_lidar(extrinsics_df):
#     """Per lidar, compute the extrinsics delta transform and mileage delta"""
#     delta_extrinsics_df = pd.DataFrame()
#     for lidar, lidar_df in extrinsics_df.groupby('lidar'):
#         for (a, row_a), (b, row_b) in itertools.combinations(lidar_df.iterrows(), 2):
#             delta_non_numeric = pd.Series({
#                 'meta_id_a': row_a['meta_id'],
#                 'meta_id_b': row_b['meta_id'],
#                 'lidar': lidar
#             })
#             delta_numeric = row_b[numeric_columns] - row_a[numeric_columns]
#             delta_extrinsics_df = delta_extrinsics_df.append(delta_non_numeric.append(delta_numeric), ignore_index=True)

#     # hardcode column order
#     # sort by lidar number first, then by miles
#     # after sorting the index is no longer sorted. This resets it.
#     return delta_extrinsics_df[non_numeric_columns + numeric_columns] \
#         .sort_values(by=['lidar', 'miles'])                    \
#         .reset_index(drop=True)

# def get_adj_delta_extrinsics_per_lidar(extrinsics_df):
#     """Per lidar, compute the extrinsics delta transform and mileage delta between adjacent calibrations"""
#     delta_extrinsics_df = pd.DataFrame()
#     for lidar, lidar_df in extrinsics_df.groupby('lidar'):
#         for (a, row_a), (b, row_b) in pairwise(lidar_df.iterrows()):
#             delta_non_numeric = pd.Series({
#                 'meta_id_a': row_a['meta_id'],
#                 'meta_id_b': row_b['meta_id'],
#                 'lidar': lidar
#             })
#             delta_numeric = row_b[numeric_columns] - row_a[numeric_columns]
#             delta_extrinsics_df = delta_extrinsics_df.append(delta_non_numeric.append(delta_numeric), ignore_index=True)

#     return delta_extrinsics_df[non_numeric_columns + numeric_columns] \
#         .sort_values(by=['lidar', 'miles'])                    \
#         .reset_index(drop=True)
        
def get_rel_first_delta_extrinsics_per_lidar(extrinsics_df):
    """
    Per lidar, compute the extrinsics delta transform and mileage delta between each calibration against the first calibration
    L_1^a T L_1^b for all b in runs
    """
    delta_extrinsics_df = pd.DataFrame()
    for lidar, lidar_df in extrinsics_df.groupby('lidar'):
        rows = lidar_df.iterrows()
        a, row_a = rows.next()
        for (b, row_b) in rows:
            delta_non_numeric = pd.Series({
                'meta_id_a': row_a['meta_id'],
                'meta_id_b': row_b['meta_id'],
                'lidar': lidar
            })
            delta_numeric = row_b[numeric_columns] - row_a[numeric_columns]
            delta_extrinsics_df = delta_extrinsics_df.append(delta_non_numeric.append(delta_numeric), ignore_index=True)

    return delta_extrinsics_df[non_numeric_columns + numeric_columns] \
        .sort_values(by=['lidar', 'miles'])                    \
        .reset_index(drop=True)
        

def show_df(df):
    df = df.copy()
    df['roll_deg'], df['pitch_deg'], df['yaw_deg'] = np.degrees(df['roll']), np.degrees(df['pitch']), np.degrees(df['yaw'])
    px.line(df, x='miles', y='x', color='lidar').show()
    px.line(df, x='miles', y='y', color='lidar').show()
    px.line(df, x='miles', y='z', color='lidar').show()
    px.line(df, x='miles', y='roll_deg', color='lidar').show()
    px.line(df, x='miles', y='pitch_deg', color='lidar').show()
    px.line(df, x='miles', y='yaw_deg', color='lidar').show()
        

# delta_extrinsics_df = get_delta_extrinsics_per_lidar(extrinsics_df)
# adj_delta_extrinsics_df = get_adj_delta_extrinsics_per_lidar(extrinsics_df)
rel_first_delta_extrinsics_L = get_rel_first_delta_extrinsics_per_lidar(extrinsics_L)
rel_first_delta_extrinsics_BL = get_rel_first_delta_extrinsics_per_lidar(extrinsics_df)

In [ ]:
extrinsics_df[extrinsics_df['lidar'] == "FRONT_LOWER_CENTER"]

In [ ]:
even_scaled = pd.DataFrame(list(itertools.product([-5, 5], repeat=3)), columns=list('xyz'))
even_scaled['lidar'] = .001
px.scatter_3d(extrinsics_df.append(even_scaled), x="x", y="y", z="z", color="lidar")

## There are 6 calibrations. For each lidar, the difference between xyz rpy extrinsics between each of the last 5 calibrations against the first calibration is plotted in the following plots below.

In [ ]:
# show_df(delta_extrinsics_df)
# show_df(adj_delta_extrinsics_df)
# show_df(rel_first_delta_extrinsics_L)
show_df(rel_first_delta_extrinsics_BL)